In [0]:
import requests, json, re
import numpy as np
import pandas as pd
from pyspark.sql.functions import current_timestamp, col, udf
from pyspark.sql.types import IntegerType, StringType

In [0]:
%run "/Workspace/Users/n01606417@humber.ca/etl_project/utils/Common Variables"

In [0]:
dbutils.secrets().listScopes()

[SecretScope(name='amazon-products-secret-scope'),
 SecretScope(name='ecommerce-transactions_secret_scope'),
 SecretScope(name='flight-data-secret-scope'),
 SecretScope(name='formula1-dl-secret-scope'),
 SecretScope(name='formula1-secret-scope'),
 SecretScope(name='openweathermap-api-key')]

In [0]:
rapid_api_key = str(dbutils.secrets.get(scope='amazon-products-secret-scope',key='amazon-products-rapidapi-key'))
rapid_api_key

'[REDACTED]'

In [0]:
def get_data(query):
  url = "https://amazon-online-data-api.p.rapidapi.com/search"

  querystring = {"query": query,
                 "page":"1",
                 "geo":"US"}
  headers = {
    "x-rapidapi-key": rapid_api_key,
    "x-rapidapi-host": "amazon-online-data-api.p.rapidapi.com"
  }

  response = requests.get(url, headers=headers, params=querystring)
  return json.loads(response.text)

In [0]:
categories = ['phone', 'laptop', 'tablet', 'camera', 'headphones', 'tv', 'airpods', 'charger', 'earbuds', 'speaker', 'keyboard', 'mouse', 'monitor', 'mousepad', 'pendrive', 'shared_drive', 'memory_card', 'powerbank', 'charging_case', 'charging_stand', 'charging_cable', 'charging_kit', 'charging_stand', 'charging_cable', 'shampoo', 'conditioner', 'hair_gel', 'hair_spray', 'hair_conditioner', 'hair_oil', 'hair_serum', 'hair_mask', 'hair_treatment', 'hair_color', 'hair_dryer', 'iphone_case', 'iphone_cover', 'iphone_charger', 'iphone_cable', 'iphone_earbuds', 'iphone_headphones', 'iphone_speaker', 'iphone_screen_protector', 'iphone_earpiece', 'iphone_earpiece_case', 'iphone_earpiece_stand', 'bottle', 'water', 'juice', 'shampoo', 'conditioner', 'hair_gel', 'hair_spray', 'hair_conditioner', 'hair_oil', 'basket', 'baby_bottle', 'baby_water', 'baby_shampoo', 'baby_conditioner', 'baby_hair_gel', 'baby_hair_spray', 'baby_hair_conditioner', 'baby_hair_oil', 'baby_hair_serum', 'baby_hair_mask', 'baby_hair_treatment', 'baby_hair_color', 'wardrobe', 'wardrobe_shoes', 'wardrobe_clothing', 'wardrobe_jewellery', 'wardrobe_bags', 'wardrobe_hats']
categories = list(set(categories))
len(categories)

66

In [0]:
data = get_data('phone')

In [0]:
data.keys()

dict_keys(['amazon_request_count', 'metadata', 'products', 'success'])

In [0]:
pd.json_normalize(data['products']).head()

asin  ...               sales_volume
0  B0CP6DDN1H  ...   1K+ bought in past month
1  B0D1ZFS9GH  ...   1K+ bought in past month
2  B0CV4NQYFP  ...   3K+ bought in past month
3  B0BZG14KFJ  ...   5K+ bought in past month
4  B0CMDL3H3P  ...  400+ bought in past month

[5 rows x 16 columns]

In [0]:
products_df = pd.DataFrame()

for category in categories:
  data = get_data(category)
  df = pd.json_normalize(data['products'])
  products_df = pd.concat([products_df,df],axis=0)
  if products_df.shape[0] == 0:
    break
  print(f"Category {category} done.")

Category iphone_case done.
Category baby_hair_oil done.
Category keyboard done.
Category mousepad done.
Category iphone_speaker done.
Category charging_cable done.
Category wardrobe_jewellery done.
Category iphone_earpiece_stand done.
Category baby_conditioner done.
Category mouse done.
Category wardrobe_clothing done.
Category laptop done.
Category iphone_earbuds done.
Category wardrobe_bags done.
Category tv done.
Category hair_mask done.
Category hair_gel done.
Category bottle done.
Category baby_bottle done.
Category wardrobe_shoes done.
Category tablet done.
Category camera done.
Category shared_drive done.
Category baby_hair_conditioner done.
Category baby_hair_color done.
Category pendrive done.
Category phone done.
Category charging_kit done.
Category iphone_cover done.
Category water done.
Category baby_hair_spray done.
Category conditioner done.
Category hair_serum done.
Category charger done.
Category baby_hair_gel done.
Category hair_oil done.
Category speaker done.
Categor

In [0]:
for category in list(set(['apparel','electronics','furniture','sports','hoodies','jackets','jeans','shoes','sneakers','watches','accessories','shirts','t-shirts','tops','trousers','skirts','blazers','pants','shorts','dresses','bags','hats','sunglasses','scarves','socks','underwear','swimwear','sweaters','leggings','sweaters'])):
  if category not in categories:
    data = get_data(category)
    df = pd.json_normalize(data['products'])
    products_df = pd.concat([products_df,df],axis=0)
    if df.shape[0] == 0:
      break
    print(f"Category {category} done.")

Category tops done.
Category shoes done.
Category sweaters done.
Category shirts done.
Category underwear done.
Category electronics done.
Category leggings done.
Category swimwear done.
Category trousers done.
Category scarves done.
Category furniture done.
Category apparel done.
Category t-shirts done.
Category skirts done.
Category blazers done.
Category jackets done.
Category hoodies done.
Category watches done.
Category pants done.
Category dresses done.
Category accessories done.
Category sunglasses done.
Category shorts done.
Category socks done.
Category sports done.
Category jeans done.
Category sneakers done.
Category hats done.
Category bags done.


In [0]:
products_df.shape

(3520, 16)

In [0]:
products_df.head()

asin  ...               sales_volume
0  B099JVC9HL  ...  10K+ bought in past month
1  B0CGCMS31N  ...   9K+ bought in past month
2  B0CPXNLBSX  ...   3K+ bought in past month
3  B08DY8GJN4  ...   5K+ bought in past month
4  B0B7C9SPSF  ...   5K+ bought in past month

[5 rows x 16 columns]

In [0]:
products_df = spark.createDataFrame(products_df)
products_df.printSchema()

root
 |-- asin: string (nullable = true)
 |-- climate_pledge: boolean (nullable = true)
 |-- is_amazon_choice: boolean (nullable = true)
 |-- is_best_seller: boolean (nullable = true)
 |-- is_prime: boolean (nullable = true)
 |-- offers_count: string (nullable = true)
 |-- product_delivery_info: string (nullable = true)
 |-- product_num_ratings: string (nullable = true)
 |-- product_original_price: string (nullable = true)
 |-- product_photo: string (nullable = true)
 |-- product_price: string (nullable = true)
 |-- product_star_rating: string (nullable = true)
 |-- product_stock_message: string (nullable = true)
 |-- product_title: string (nullable = true)
 |-- product_url: string (nullable = true)
 |-- sales_volume: string (nullable = true)



In [0]:
products_df.count()

3520

In [0]:
products_df.describe().show()

+-------+--------------------+------------------+---------------------+-------------------+----------------------+--------------------+------------------+-------------------+---------------------+--------------------+--------------------+--------------------+
|summary|                asin|      offers_count|product_delivery_info|product_num_ratings|product_original_price|       product_photo|     product_price|product_star_rating|product_stock_message|       product_title|         product_url|        sales_volume|
+-------+--------------------+------------------+---------------------+-------------------+----------------------+--------------------+------------------+-------------------+---------------------+--------------------+--------------------+--------------------+
|  count|                3520|              3520|                 3496|               3468|                  2890|                3520|              3506|               3468|                  122|                3520|   

In [0]:
display(products_df)

asin climate_pledge is_amazon_choice is_best_seller is_prime offers_count product_delivery_info product_num_ratings product_original_price product_photo product_price product_star_rating product_stock_message product_title product_url sales_volume B099JVC9HL false false true true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 99,755 30.99 https://m.media-amazon.com/images/I/51rRDJJRtSL._AC_UY218_.jpg 13.29 4.6 null ESR for iPhone 14 Case/iPhone 13 Case, Compatible with MagSafe, Shockproof Military-Grade Protection, Magnetic Phone Case for iPhone 14/13, Classic Hybrid Case (HaloLock), Clear https://www.amazon.com/ESR-Compatible-Military-Grade-Protection-Scratch-Resistant/dp/B099JVC9HL 10K+ bought in past month B0CGCMS31N false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliveryTue, Nov 26 1,379 39.95 https://m.media-amazon.com/images/I/71Go+X-xMOL._AC_UY218_.jpg 27.97 4.6 null OtterBox iPhone 15, iPhone 14, and iPhone 13 Commuter Series Case - Black, Slim & Tough, Pocket-Friendly, with Port Protection https://www.amazon.com/OtterBox-iPhone-Commuter-Case-pocket-friendly/dp/B0CGCMS31N 9K+ bought in past month B0CPXNLBSX false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 2,097 null https://m.media-amazon.com/images/I/61rdZoMRrGL._AC_UY218_.jpg 12.98 4.5 null BENTOBEN Magnetic for iPhone 13 Case & iPhone 14 Case [Compatible with Magsafe] Translucent Matte Phone Case iPhone 13/14 Slim Fit Shockproof Women Men Protective Cover for iPhone 13/14 6.1", Hot Pink https://www.amazon.com/BENTOBEN-Compatible-Translucent-Shockproof-Protective/dp/B0CPXNLBSX 3K+ bought in past month B08DY8GJN4 false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 20,827 39.95 https://m.media-amazon.com/images/I/81pqBkXzjOL._AC_UY218_.jpg 19.94 4.7 null OtterBox iPhone 12 & iPhone 12 Pro Commuter Series Case - Black, Slim & Tough, Pocket-Friendly, with Port Protection https://www.amazon.com/OtterBox-Commuter-Case-iPhone-Pro/dp/B08DY8GJN4 5K+ bought in past month B0B7C9SPSF false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 2,065 39.95 https://m.media-amazon.com/images/I/61enjLcjnUL._AC_UY218_.jpg 27.96 4.7 null OtterBox iPhone 14 & iPhone 13 Commuter Series Case - Black, Slim & Tough, Pocket-Friendly, with Port Protection https://www.amazon.com/OtterBox-COMMUTER-iPhone-14-13/dp/B0B7C9SPSF 5K+ bought in past month B0CKT6JGX6 false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliveryMon, Nov 25 1,333 9.999.99 https://m.media-amazon.com/images/I/51d-yylRPyL._AC_UY218_.jpg 7.99 4.6 null Vooii Compatible with iPhone 13 Case, Liquid Silicone Upgrade [Camera Protection] [Soft Anti-Scratch Microfiber Lining] Shockproof Phone Case for iPhone 13 6.1 inch - Stone https://www.amazon.com/Vooii-Compatible-Protection-Anti-Scratch-Microfiber/dp/B0CKT6JGX6 500+ bought in past month B0D944B4GS false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 7,586 8.998.99 https://m.media-amazon.com/images/I/61Z9OFrXi4L._AC_UY218_.jpg 7.64 4.6 null Temdan for iPhone 16 Pro Case Clear, [Compatible with Magsafe][Anti-Yellowing][Military-Grade Protection] Shockproof Slim Magnetic Phone Case for iPhone 16 Pro, Transparent https://www.amazon.com/Temdan-Compatible-Anti-Yellowing-Military-Grade-Transparent/dp/B0D944B4GS 10K+ bought in past month B0DD6DH27Y false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 138 44.95 https://m.media-amazon.com/images/I/71yxtCE+-7L._AC_UY218_.jpg 31.47 4.1 null OtterBox iPhone 16 Pro Commuter Series Case - Black https://www.amazon.com/OtterBox-iPhone-Pro-Commuter-Case/dp/B0DD6DH27Y 4K+ bought in past month B09D55YMC1 false false false true 1

In [0]:
products_df.write.format("csv").option("header", "true").mode("overwrite").save(f'{raw_folder_path}/products.csv')

In [0]:
products_df = spark.read.csv(f"{raw_folder_path}/products.csv",header=True,inferSchema=True)
display(products_df)

asin climate_pledge is_amazon_choice is_best_seller is_prime offers_count product_delivery_info product_num_ratings product_original_price product_photo product_price product_star_rating product_stock_message product_title product_url sales_volume B0DFH7N4ST false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 4 null https://m.media-amazon.com/images/I/51JJqCSYFYL._AC_UY218_.jpg 9.99 5.0 null Multi USB Charging Adapter Cable Kit, USB C to Ligh-ting Adapter Box, Conversion Set USB A Type C Lightn-ing Micro Adapter Kit,60W Charging and Data Transfer Cable Kit Sim Tray Eject Tool Slots https://www.amazon.com/Charging-Ligh-ting-Conversion-Lightn-ing-Transfer/dp/B0DFH7N4ST null B0BLH2Q3PV false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 898 4.254.25 https://m.media-amazon.com/images/I/616VZ+RXXnL._AC_UY218_.jpg 16.99 4.2 null 4 Pcs 3 in 1 Charging Cable, Three in one Retractable Multi Charging Cable with USB C(Type-C)/Micro USB, Phone Holder, Compatible with Phone/Android/Tablet (Red+Blue+Green+Black) https://www.amazon.com/Gartmost-Charging-Transfer-Retractable-Compatible/dp/B0BLH2Q3PV 500+ bought in past month B0D13CYYMQ false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 7 null https://m.media-amazon.com/images/I/61hbC2QF4uL._AC_UY218_.jpg 5.99 4.0 null Multi USB Charging Adapter Cable Kit, USB to USB C Adapter and Sim Card Adapter Conversion Set, USB C to USB Adapter Box, USB C to Micro USB Adapter and Phone Holder for Traveling https://www.amazon.com/ILZAR-Charging-Adapter-Conversion-Traveling/dp/B0D13CYYMQ null B08C5KW5NK false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 4,399 1.371.37 https://m.media-amazon.com/images/I/71VnzBoCVgL._AC_UY218_.jpg 10.99 4.4 null Multi Charging Cable,3.5A Multi Charger Cable,Braided 4 in 1 Charging Cable,Multi USB Cable, Fast Charging Cord with IP/Type C/Micro USB Port for Cell Phones/Tablets/Samsung Galaxy & More(2Pack 4Ft) https://www.amazon.com/Minlu-Charger-Charging-Adapter-Tablets/dp/B08C5KW5NK 3K+ bought in past month B0CQYJVJDR false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 905 59.95 https://m.media-amazon.com/images/I/51Z8hS3IupL._AC_UY218_.jpg 33.96 4.6 null USB C Charger 200W USB C Charger Block,Upgraded GaN III 8-Port Fast Charging Station Hub,PD 65W Laptop Charger Adapter Compatible with MacBook Pro/Air,DELL,Steam Deck,iPhone 16/15/14,Galaxy S23/22 etc https://www.amazon.com/Charger-Upgraded-Charging-Station-Compatible/dp/B0CQYJVJDR 6K+ bought in past month B09NY3RSJ2 false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 7,844 4.814.81 https://m.media-amazon.com/images/I/61vpOd+b0pL._AC_UY218_.jpg 14.44 4.6 null CSODINCE 3 Pack USB C Wall Charger, 20W Durable Dual Port QC+PD 3.0 Power Adapter, Double Fast Plug Charging Block for iPhone 14/14 Pro/13/15/15 Pro/Pro Max/Plus, XS/XR/X, Watch Series 8/7 Cube，White https://www.amazon.com/Charger-Upgraded-Certified-Durable-AirPods/dp/B09NY3RSJ2 9K+ bought in past month B0CG1T2GC8 false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliveryMon, Nov 25 274 null https://m.media-amazon.com/images/I/61r7e2BK-UL._AC_UY218_.jpg 5.29 4.5 null USB C to Lightning Adapter, USB C Adapter Kit Contains Multiple OTG Adapters for Type C to Lightning, USB A to USB C Male Cable, Micro USB to Type C, Equipped with SIM Extractor and Phone Stand https://www.amazon.com/Charging-Contains-Multiple-Adapters-Extractor/dp/B0CG1T2GC8 300+ bought in past month B0B17HR2LL false false false true 1 FREE deliveryWed, Nov 27on $35 of items shipped by AmazonOr fastest deliverySun, Nov 24 8,949 29.99 https://m.media-amazon.com/images/I/61KOOcj58rL._AC_UY218_.jpg 18.98 